Author: Colm Yeh, yehcolum@gmail.com
<br>
Stakeholder: Olist E-commerce
<br>
Methods: Geospatial Analysis, Segmentation Analysis, and Time Series Forecasting

In [ ]:
asdfadsfasdfasdfasdfasdfasdf

# Overview

What will Olist's future sales look like? From which kind of customer and from which region will they occur?
<br>

Moreover, which regions are the most valuable to the company in terms of total customers and total sales?

# Business Problem

Managers at Olist need to understand future demand in number and geography in order to properly allocate capital across their operations. 
<br> 
This analysis seeks to analyze sales data across Brazils' states to drive actionable insight. My method will consist of 3 objectives:
<br>
1. Geospatial Analysis
2. Segmentation Analysis
3. Time Series Forecasting of Sales
<br>

Finally, I will provide recommendations on where to allocate capital to best position the firm to provide value for its customers.

# The Data

The data schema above visualizes the data sets we will be analyzing. Foreign keys are indicated by the arrows. 

# Data Preprocessing and EDA

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
import seaborn as sns
from sklearn.metrics import calinski_harabasz_score, adjusted_rand_score
from sklearn.cluster import AgglomerativeClustering
from sklearn.decomposition import PCA
from statsmodels.graphics.tsaplots import plot_acf
from statsmodels.graphics.tsaplots import plot_pacf
from pmdarima.arima import auto_arima
from statsmodels.tsa.seasonal import seasonal_decompose

In [ ]:
!pip install pmdarima

In [ ]:
#load in all data as pandas dataframes
df_customers = pd.read_csv("/content/olist_customers_dataset.csv")
df_geolocation = pd.read_csv("/content/olist_geolocation_dataset.csv")
df_orderitems= pd.read_csv("/content/olist_order_items_dataset.csv")
df_payments= pd.read_csv("/content/olist_order_payments_dataset.csv")
df_products= pd.read_csv("/content/olist_products_dataset.csv")
df_sellers= pd.read_csv("/content/olist_sellers_dataset.csv")
df_translation= pd.read_csv("/content/product_category_name_translation.csv")
df_orders = pd.read_csv("/content/olist_orders_dataset.csv")

In [ ]:
df_reviews = pd.read_csv("/content/olist_order_reviews_dataset.csv")

In [ ]:
df_orderitems.head()

In [ ]:
df_orders.head()

In [ ]:
df_customers.head()

In [ ]:
df_customers['customer_city'].unique()

In [ ]:
df_customers['customer_city'].value_counts()

Citites in southern Brazil have significantly more customers than the more rural north-northwest. Southern Brazil appears to be our center of operations.

In [ ]:
df_geolocation.head()

In [ ]:
df_sellers.head()

In [ ]:
df_sellers['seller_city'].value_counts()

Seller counts confirm that Olist's hub of operations is in southern Brazil. Geospatial analysis below will confirm this, and examine the nature of the southern hub.

In [ ]:
#simplify column name
df_geolocation.rename(columns={'geolocation_zip_code_prefix':'zip_code'}, inplace=True)

In [ ]:
#simplify column name
df_customers.rename(columns={'customer_zip_code_prefix':'zip_code'}, inplace=True)

In [ ]:
df_geolocation.head()

In [ ]:
#put dataframes together via .merge() method
df = df_orders.merge(df_customers, on="customer_id").merge(df_orderitems, on="order_id").merge(df_products, on="product_id").merge(df_translation, on="product_category_name").merge(df_payments, on="order_id").merge(df_sellers, on="seller_id").merge(df_reviews, on="order_id")

In [ ]:
df.head()

In [ ]:
df.columns

In [ ]:
!pip install -U pandas-profiling

In [ ]:
from pandas_profiling import ProfileReport

In [ ]:

eda = ProfileReport(df, title='EDA report')

In [ ]:
eda.to_notebook_iframe()

Pandas profile revealed some interesting insights on the breadth of the dataset and the correlations among variables:
<br>
1. Our dataset contains over 96K unique order id's collected since 2017 across 27 states, 4,093 cities, and 14,907 zip codes. 
<br>
2. Correlations:
<br>
<b>frieght_value and product_weight</b> are highly correlated. This makes sense, as heavier porducts will be more expensive to move, resulting in higher freight value.
<br>
<b>price/payment_value and the size of the product (product length, height, width, weight) </b>are highly correlated. Larger products tend to be more expensive, resulting in higher prices and payment values. 
<br>
3. Across 71 product categories, the top 5 by order count include bed_bath_beauty, health_beauty, sports_leisure, furniture_decor, and computer_accessories. The top 10 categories by revenue is explored below. 



In [ ]:
#groupby category and total payment value
df_cat = df.groupby(by='product_category_name', as_index=False)['payment_value'].sum()
df_cat.head()

In [ ]:
#visualize
sns.catplot(data=df_cat, x='product_category_name', y='payment_value', kind='bar', height=15, aspect=20/15)
plt.xticks(rotation=70)
plt.tight_layout()

In [ ]:
df_cat['payment_value'].nlargest(n=10)

In [ ]:
#extract top 10 categories by revenue
top10 = df_cat.iloc[[13, 11, 44, 54, 64, 32, 70, 40, 8, 26]]
top10

In [ ]:
#visualize top 10 categories
sns.catplot(data=top10, x='product_category_name', y='payment_value', kind='bar', height=15, aspect=20/15)
plt.xticks(rotation=70)
plt.tight_layout()

Top 10 categories by revenue are visualized above. Bed_bath_table is our largest category at BR 1.7 million. Beauty and computer accessories follow at BR 1.64 million and 1.59 million, respectively. 

In [ ]:
#visualize payment type 
sns.countplot(df['payment_type'])

Majority of purchases are made with credit cards, with boletos (Brazilian cash payment method) taking second place.

In [ ]:
df['payment_value'].head(20)

In [ ]:
df['review_score'].value_counts()

In [ ]:
#visualize review scores
sns.countplot(df['review_score'])

Review scores are skewed left, indicating mostly positive (4 or 5) reviews. 

In [ ]:
df["review_score"].value_counts() / df["review_score"].count() * 100

Over 75% of reviews can be considered positive (4 or 5). 

In [ ]:
df['seller_city'].value_counts()

In [ ]:
import datetime

# Recency, Frequency, Monetary Clustering
<br>

RFM analysis examines customers across 3 characteristics: recency, frequency, and monetary value. 

1. Recency: how recent a customer purchased
2. Frequency: how frequent a customer purchases
3. Monetary: how valuable the customer purchases are

<br>
To this end, I will now create data frames to look at each characteristic.

In [ ]:
#Recency dataframe
recencydf = df.groupby(by='customer_unique_id', as_index=False)['order_purchase_timestamp'].max()
recencydf.head()

In [ ]:
recencydf.info()

In [ ]:
#change from object to dt
recencydf['order_purchase_timestamp'] = pd.to_datetime(recencydf['order_purchase_timestamp'], infer_datetime_format=True)
recencydf.head()

In [ ]:
recencydf.info()

In [ ]:
#change to string to eliminate secs, hours, millisec
recencydf['order_purchase_timestamp'] = recencydf['order_purchase_timestamp'].dt.strftime('%Y-%m-%d')

In [ ]:
recencydf['order_purchase_timestamp'] = pd.to_datetime(recencydf['order_purchase_timestamp'])


In [ ]:
recencydf.info()

In [ ]:
#create today in order to find difference
today = recencydf['order_purchase_timestamp'].max()
today

In [ ]:
#create recency column
recencydf['Recency'] = today - recencydf['order_purchase_timestamp'] 
recencydf.head()

In [ ]:
#create monetary dataframe
monetarydf = df.groupby(by='customer_unique_id', as_index=False)['payment_value'].sum()
monetarydf.head()

In [ ]:
#create frequency dataframe
frequencydf = df.groupby(["customer_unique_id"]).agg({"order_id":"nunique"}).reset_index()
frequencydf.rename(columns={'order_id': 'frequency'}, inplace=True)
frequencydf.head()

In [ ]:
#combine into RFM dataframe
FM = monetarydf.merge(frequencydf, on='customer_unique_id')
FM

In [ ]:
RFM = FM.merge(recencydf, on='customer_unique_id')
RFM.head()

In [ ]:
RFM = RFM.drop(columns='order_purchase_timestamp')
RFM.head()

In [ ]:
RFM.describe()

Average payment value equals 213 with relatively large standard deviation at 631. Average frequency equals slightly above one, indicating that most customers order one item. Moreover, an average recency of 242 days indicates that most customers seem to only buy once a year(ish).

## Clustering
<br>
Now, I will fit a K-means clustering model to the data. This unsupervised learning technique will produce customer segments according to recency, frequency, and monetary value. Each model will be iteratively improved with scaling, transformations, and principle component analysis (PCA). 
<br>

The best model will be selected according to the variance ratio.

In [ ]:
#indext to customer id
RFM.set_index('customer_unique_id', inplace=True)

In [ ]:
RFM.head()

In [ ]:
#Change recency values to object in order to remove datetime delta type
RFM['Recency'] = RFM['Recency'].astype('str')
RFM.info()

In [ ]:
#only show day values in order to change into int
RFM['Recency'] = RFM['Recency'].str[:-5]
RFM.head()

In [ ]:
#recency_df['order_purchase_timestamp'] = recency_df['order_purchase_timestamp'].dt.strftime('%Y-%m-%d')

In [ ]:
RFM.info()

In [ ]:
#change to int in order to run clustering model
RFM['Recency'] = RFM['Recency'].astype(int)

In [ ]:
RFM.info()

In [ ]:
RFM.head()

In [ ]:
#fit kmeans model with different n_clusters
k_means_2 = KMeans(n_clusters=2).fit(RFM)
k_means_3 = KMeans(n_clusters=3).fit(RFM)
k_means_4 = KMeans(n_clusters=4).fit(RFM)
k_means_5 = KMeans(n_clusters=5).fit(RFM)
k_means_6 = KMeans(n_clusters=6).fit(RFM)
k_means_7 = KMeans(n_clusters=7).fit(RFM)
k_means_8 = KMeans(n_clusters=8).fit(RFM)
k_means_9 = KMeans(n_clusters=9).fit(RFM)
k_means_10 = KMeans(n_clusters=10).fit(RFM)

k_list = [k_means_2, k_means_3, k_means_4, k_means_5, k_means_6, k_means_7, k_means_8, k_means_9,
         k_means_10]

In [ ]:
#store Calinski scores
CH_score = []

for model in k_list:
    labels = model.labels_
    CH_score.append(calinski_harabasz_score(RFM, labels))

In [ ]:
CH_score

In [ ]:
#plot CH score to find optimal cluster value
plt.plot([2, 3, 4, 5, 6, 7, 8, 9, 10], CH_score)
plt.xticks([2,3,4,5,6,7,8,9,10])
plt.title('Calinski Harabasz Scores for Different Values of K')
plt.ylabel('Variance Ratio')
plt.xlabel('K=')
plt.show()

In [ ]:
#store WCSS scores
wcss_score = []
for model in k_list:
    labels = model.labels_
    wcss_score.append(model.inertia_)

In [ ]:
#Plot WCSS scores to find optimal K
plt.plot([2, 3, 4, 5, 6, 7, 8, 9, 10], wcss_score)
plt.xticks([2,3,4,5,6,7,8,9,10])
plt.title('Within Cluster Sum of Squares')
plt.ylabel('WCSS')
plt.xlabel('K=')
plt.show()

In [ ]:
#predict across clusters
cluster_preds = k_means_5.predict(RFM)

In [ ]:
#return CH score
calinski_harabasz_score(RFM, cluster_preds)

Elbow plot suggests 5 clusters exist in our customer data. Further iterations will be performed to improve our clustering. The baseline CH score stands at 105,287.98.

In [ ]:
RFM.isna().value_counts()

In [ ]:
RFM.head()

In [ ]:
#scale data using StandardScaler()
scaler = StandardScaler()
scaled_RFM = scaler.fit_transform(RFM)
scaled_RFM


In [ ]:
#fit KMeans model to scaled data across various n_clusters
scaled_kmeans3 = KMeans(n_clusters=3).fit(scaled_RFM)
scaled_kmeans4 = KMeans(n_clusters=4).fit(scaled_RFM)
scaled_kmeans5 = KMeans(n_clusters=5).fit(scaled_RFM)
scaled_kmeans6 = KMeans(n_clusters=6).fit(scaled_RFM)

scaled_kmeans = [scaled_kmeans3, scaled_kmeans4, scaled_kmeans5, scaled_kmeans6]

In [ ]:
#store scaled CH scores
CH_score_scaled = []

for model in scaled_kmeans:
    labels = model.labels_
    CH_score_scaled.append(calinski_harabasz_score(scaled_RFM, labels))

In [ ]:
#visualize CH scores to find optimal K
plt.plot([3, 4, 5, 6], CH_score_scaled)
plt.xticks([3,4,5,6])
plt.title('Calinski Harabasz Scores for Different Values of K')
plt.ylabel('Variance Ratio')
plt.xlabel('K=')
plt.show()

In [ ]:
#store WCSS scors
wcss_score_scaled = []
for model in scaled_kmeans:
    labels = model.labels_
    wcss_score_scaled.append(model.inertia_)

In [ ]:
#visualize elbow plot for optimal K
plt.plot([3, 4, 5, 6], wcss_score_scaled)
plt.xticks([3,4,5,6])
plt.title('Within Cluster Sum of Squares')
plt.ylabel('WCSS')
plt.xlabel('K=')
plt.show()

In [ ]:
#return CH score on scaled data
scaled_cluster_preds = scaled_kmeans5.predict(scaled_RFM)
calinski_harabasz_score(scaled_RFM, scaled_cluster_preds)

Elbow plot suggests 5 clusters for scaled model. However, we observe a decrease in variance ratio for scaled data, indicating lower quality clusters. Principle component analysis (PCA) will no be implemented for the final iteration. 

In [ ]:
#initiate PCA, fit_transform data
pca = PCA()
pca_scaled = pca.fit_transform(scaled_RFM)

In [ ]:
np.cumsum(pca.explained_variance_ratio_)

In [ ]:
#fit KMeans on pca_scaled data across various n_clusters
pca_km3 = KMeans(n_clusters=3).fit(pca_scaled)
pca_km4 = KMeans(n_clusters=4).fit(pca_scaled)
pca_km5 = KMeans(n_clusters=5).fit(pca_scaled)
pca_km6 = KMeans(n_clusters=6).fit(pca_scaled)

pca_kmeans = [pca_km3, pca_km4, pca_km5, pca_km6]

In [ ]:
#store CH scores
CH_score_pca = []

for model in pca_kmeans:
    labels = model.labels_
    CH_score_pca.append(calinski_harabasz_score(pca_scaled, labels))

In [ ]:
#visualize CH scores
plt.plot([3, 4, 5, 6], CH_score_pca)
plt.xticks([3,4,5,6])
plt.title('Calinski Harabasz Scores for Different Values of K')
plt.ylabel('Variance Ratio')
plt.xlabel('K=')
plt.show()

In [ ]:
#store WCSS scores
wcss_score_pca = []
for model in pca_kmeans:
    labels = model.labels_
    wcss_score_pca.append(model.inertia_)

In [ ]:
#visulaize elbow plot to find optimal K
plt.plot([3, 4, 5, 6], wcss_score_pca)
plt.xticks([3,4,5,6])
plt.title('Within Cluster Sum of Squares')
plt.ylabel('WCSS')
plt.xlabel('K=')
plt.show()

In [ ]:
#return CH score for evaluation
pca_cluster_preds = pca_km5.predict(pca_scaled)
calinski_harabasz_score(pca_scaled, pca_cluster_preds)

Elbow plot sugggest 5 clusters. However, our baseline clustering model with n_clusters=5 maintains the best variance ratio. In other words, the intra-cluster variance compared to the inter-cluster variance is the best for our baseline model. The baseline model clusters will be examined for targeting insights. 

In [ ]:
#fit best model according to CH score
kmeans_final = KMeans(n_clusters=5).fit(RFM)
kmeans_final_preds = kmeans_final.predict(RFM)


In [ ]:
RFM['clusters'] = kmeans_final.labels_
RFM.head()

In [ ]:
#grouby clusters to examine cluster characteristics
cluster_rfm = RFM.groupby(['clusters']).agg({
            'Recency': 'mean',
            'frequency': 'mean',
            'payment_value': ['mean', 'count']
        }).round(0)

In [ ]:
cluster_rfm

Frequency does not seem to add any meaningful signal for our clusters, as most customers have a frequency of 1. The model returned 5 clusters:
<br>
0. Middle of the road monetary value with similar recency to cluster 1. These customers are similar to cluster 1, but have much higher average monetary value. These customers represent our second largest cluster by customer count, and second most valuable customer segment as a percentage of sales revenue.
1. Low monetary value with relatively high recency. As the largest of our clusters, these individuals purchase about once a year with relatively low order value. They are the largest customer segment by count and as a precentage of sales revenue.
<br>
2. High monetary value with with relatively low recency. On an individual basis, these people represent our most valuable customers. They have highest average order value and have purchased the most recently.  
<br>
3. Outlier customer who purchased a significantly large amount a long time ago. Infering from the massive order value, this customer is probably some kind of business. This customer does not fit into the other segments, so they stand alone.
<br>
4. Middle-high monetary value with lower recency. These customers' monetary values sit between clusters 0 and 2, with the second lowest recency out of all our clusters. They order with higher payment values, and also ordered more recently than our other customer segments (excluding segment 2). 
<br>

Overall, our clusters reveal an underlying problem in Olist's customer base: __low customer life-time value (LTV).__ According to our model, customers do not come back to purchase again often (frequency). Olist is failing to build meaningful relationships with their customers, resulting in lower LTV. This has serious implications on profitability. Given the often razor thin margins of e-commerce, Olist may have negative customer LTV. This means that Olist loses money on the average customer they service. Recommendations to Olist managers will attempt to address this issue and increase customer LTV.

# Geospatial Analysis
<br>
How do customers, sales, delivery times, and more vary across the regions of Brazil? This section seeks to visualize the geography of our ecommerce data.

In [ ]:
df_geolocation = pd.read_csv("/content/olist_geolocation_dataset.csv")

In [ ]:
!pip install keplergl

In [ ]:
from google.colab import output
output.enable_custom_widget_manager()

In [ ]:
from keplergl import KeplerGl

In [ ]:
df_geolocation.head()

In [ ]:
#simplify column names
df_geolocation.rename(columns = {'geolocation_lat': 'lat', 'geolocation_lng': 'lng'}, inplace=True)
df_geolocation.head()

In [ ]:
geo1 = pd.DataFrame(df_geolocation['lat'])
geo1.head()

In [ ]:
geo2 = pd.DataFrame(df_geolocation['lng'])
geo2

In [ ]:
#create lat, lng dataframe for kepler Gl imput
GEO = pd.concat([geo1, geo2], axis=1)
GEO.head()

In [ ]:
df_geolocation['geolocation_city'].value_counts()

In [ ]:
df_geolocation['geolocation_state'].value_counts()

In [ ]:
GEO = GEO.dropna()

In [ ]:
#display kepler map
kepler_map = KeplerGl(height=400)
kepler_map

In [ ]:
#add sales lat, lng
kepler_map.add_data(data=GEO, name='sales')

Unfortunately, the geolocation dataset only contains lat and lng for sales in Sao Paulo. Sales come from all over the city, thinning out as you go further outside the city. The next portion of analysis will examine metrics on a state by state basis. 

In [ ]:
df_customers.head()

In [ ]:
df_customers['customer_state'].value_counts()

In [ ]:
#group by total sales and state
gp = df.groupby('customer_state')['price'].sum().to_frame()
gp

In [ ]:
df.columns

In [ ]:
#group by freight value per state
gf = df.groupby('customer_state')['freight_value'].sum().to_frame()

In [ ]:
gf

In [ ]:
#group by seller county by state
sellC = df.groupby('seller_state')['seller_id'].count().to_frame()
sellC = sellC.rename(columns={'seller_id':'seller_count'})
sellC


Most sellers are from Sao Paulo (82417), with Minas Gerais (9014), Parana (8964), and Rio de Janeiro (4906) following. Larger urban centers in the south appear to have the most sellers, with more rural areas having fewer sellers.

In [ ]:

tmp = df[['customer_state','order_delivered_customer_date','order_delivered_carrier_date']]
tmp.head()

In [ ]:
tmp['order_delivered_customer_date'] = pd.to_datetime(tmp['order_delivered_customer_date'])

In [ ]:
tmp['order_delivered_carrier_date'] = pd.to_datetime(tmp['order_delivered_carrier_date'])

In [ ]:
tmp.info()

In [ ]:
tmp['delivery_time'] = tmp['order_delivered_customer_date'] - tmp['order_delivered_carrier_date']
tmp['delivery_time'].head(10)

In [ ]:
Dt = tmp.groupby('customer_state')['delivery_time'].mean().to_frame()
Dt.head(20)

In [ ]:
order_status = df.groupby('customer_state')['order_status'].value_counts()/df.groupby('customer_state')['order_status'].count()
order_status = order_status.unstack().fillna(0)['delivered'].to_frame()
order_status

Most states have all orders delivered. However, Alagoas and Pernambuco have delviery rates below (.90). These two coastal states sit next to each other, suggesting that the north east coastal region experiences less reliable delivery.

In [ ]:
tmp = df[['customer_state','order_delivered_customer_date','order_estimated_delivery_date']]
tmp['is_delayed'] = df['order_delivered_customer_date'] > df['order_estimated_delivery_date']
is_delayed = tmp.groupby('customer_state')['is_delayed'].sum()/tmp.groupby('customer_state')['is_delayed'].count()
is_delayed

Delayed orders appear to be in the more rural regions of Brazil. Specifically the center-north of the country. Again, the coastal regions also show delivery problems. 

In [ ]:
PT = df.groupby('customer_state')['payment_type'].value_counts().to_frame()
PT

In [ ]:
cust_C = df.groupby('customer_state')['customer_id'].count().to_frame()
cust_C = cust_C.rename(columns={'customer_id': 'customer_count'})
cust_C.head()

In [ ]:
cust_C

In [ ]:
reviewS = df.groupby('customer_state')['review_score'].mean().to_frame()
reviewS.head(10)

In [ ]:
GAnalysis = pd.merge(gp, gf, left_index=True, right_index=True, how='left')
GAnalysis.head()

In [ ]:
GAnalysis = pd.merge(GAnalysis, Dt, left_index=True, right_index=True, how='left')
GAnalysis.head()

In [ ]:
GAnalysis = pd.merge(GAnalysis, reviewS, left_index=True, right_index=True, how='left')
GAnalysis.head()

In [ ]:
GAnalysis = pd.merge(GAnalysis, order_status, left_index=True, right_index=True, how='left')
GAnalysis.head()

In [ ]:
GAnalysis = pd.merge(GAnalysis, sellC, left_index=True, right_index=True, how='left')
GAnalysis.head()

In [ ]:
GAnalysis = pd.merge(GAnalysis, cust_C, left_index=True, right_index=True, how='left')
GAnalysis.head()

In [ ]:
!pip install plotly==5.10.0

In [ ]:
import plotly.express as px
import json

In [ ]:
#open brazil JSON data for mapping
geoJ = json.load(open('/content/brazil_geo.json'))

In [ ]:
#function for creating choropleth map
def choropleth_map(data_frame, locations, geojson, color, color_continuous_scale="Viridis", height=900, width=900):
  fig = px.choropleth(data_frame=data_frame, locations=locations, geojson=geojson, color=color, color_continuous_scale=color_continuous_scale, scope='south america')
  fig.update_layout(height=height, width=width, title='Brazilian Olist Map')
  fig.show()

In [ ]:
choropleth_map(GAnalysis, locations=GAnalysis.index, geojson=geoJ, color='customer_count')

Sao Paulo, Minas Gereis, and Rio de Janeiro hold the majority of customers. Sao Paulo appears to be the center of operations for Olist; the state boasts 48.7K customers. This is significantly higher than any other region. More rural areas in the north appear to have much fewer customers than the more urban southeast.

In [ ]:
choropleth_map(GAnalysis, locations=GAnalysis.index, geojson=geoJ, color='review_score')

Review scores are at or above 4.0 in the south. The middle and north of the country experience lower review scores, proabaly due to the more rural and remote deliveries.

In [ ]:
choropleth_map(GAnalysis, locations=GAnalysis.index, geojson=geoJ, color='freight_value' )

Freight value is much higher for Sao Pualo, Rio, and Minas Gereis. This coincides with the customer count examined earlier. The South east appears to be a bulk of Olist's freight value.

In [ ]:
#choropleth_map(GAnalysis, locations=GAnalysis.index, geojson=geoJ, color='delivery_time')

In [ ]:
choropleth_map(GAnalysis, locations=GAnalysis.index, geojson=geoJ, color='price')

Again, the urban centers of Sao Paulo, Rio de Janerio, and Minas Gereis show the largest numbers. A majority of revenue comes from these three regions. Revenue drops as one progresses north through the country. 

In [ ]:
choropleth_map(GAnalysis, locations=GAnalysis.index, geojson=geoJ, color='seller_count')

Correlating with customer count, sellers are also concentrated in the south of the country. Sao Pualo holds a vast majority of sellers at 82.6K. For sellers, Sao Paulo is the most important region. 

In [ ]:
choropleth_map(GAnalysis, locations=GAnalysis.index, geojson=geoJ, color='delivered')

# Time Series Forecasting of Demand: customer and payment value

In [ ]:
df.head()

In [ ]:
df_ts = df.copy()
df_ts.head()

In [ ]:
#change to datetime type
df_ts['order_purchase_timestamp'] = pd.to_datetime(df_ts['order_purchase_timestamp'], infer_datetime_format=True)
df_ts.head()

In [ ]:
df_ts.info()

In [ ]:
#put into string format in order to change date format
df_ts['order_purchase_timestamp'] = df_ts['order_purchase_timestamp'].dt.strftime('%Y-%m-%d')

In [ ]:
df_ts['order_purchase_timestamp'].head()

In [ ]:
df_ts['payment_value'].max()

In [ ]:
#change modified dates back into datetime type
df_ts['order_purchase_timestamp'] = pd.to_datetime(df_ts['order_purchase_timestamp'], infer_datetime_format=True)
df_ts['order_purchase_timestamp'].head()

In [ ]:

#group by total payment value received per timestamp
ts = df_ts.groupby(by='order_purchase_timestamp', as_index=True)['payment_value'].sum().to_frame()
ts.head()

In [ ]:
ts.info()

In [ ]:
ts.isnull().value_counts()

In [ ]:
#resample to weekly revenue
ts_weekly = ts.resample('W').sum()

In [ ]:
ts_weekly.shape

In [ ]:
#visualize weekly sales revenue
ts_weekly.plot(figsize=(22,15))

Preliminary visualization of our weekly sales data shows a sudden drop to zero in sales. The model may not capture the sudden drop in a train-test split. Validation will not be as clear in this situation due to the outlier event. 

In [ ]:
ts_weekly.describe()

Average weekly sales revenue stands at 188014.48(BRL). However, the standard deviation of sales revenue = 134951.3(BRL), which is a relatively high. The volatility in sales data is expected, given our previous visualization. 

In [ ]:
#check for stationarity
def stationarity_check(TS):
    
    # Import adfuller
    from statsmodels.tsa.stattools import adfuller
    
    # Calculate rolling statistics
    roll_mean = TS.rolling(window=8, center=False).mean()
    roll_std = TS.rolling(window=8, center=False).std()
    
    # Perform the Dickey Fuller test
    dftest = adfuller(TS) 
    
    # Plot rolling statistics:
    fig = plt.figure(figsize=(12,6))
    orig = plt.plot(TS, color='blue',label='Original')
    mean = plt.plot(roll_mean, color='red', label='Rolling Mean')
    std = plt.plot(roll_std, color='black', label = 'Rolling Std')
    plt.legend(loc='best')
    plt.title('Rolling Mean & Standard Deviation')
    plt.show(block=False)
    
    # Print Dickey-Fuller test results
    print('Results of Dickey-Fuller Test: \n')

    dfoutput = pd.Series(dftest[0:4], index=['Test Statistic', 'p-value', 
                                             '#Lags Used', 'Number of Observations Used'])
    for key, value in dftest[4].items():
        dfoutput['Critical Value (%s)'%key] = value
    print(dfoutput)
    
    return None

In [ ]:
stationarity_check(ts_weekly)

Dickey-Fuller test indicates the time series is non-stationary, suggesting AR and/or MA terms required for modeling. 

In [ ]:
ts_weekly.max()

In [ ]:
#Plot afc and pacf
fig, ax = plt.subplots(figsize=(16,3))
plot_acf(ts_weekly, ax=ax, lags=40);

fig, ax = plt.subplots(figsize=(16,3))
plot_pacf(ts_weekly, ax=ax, lags=40);

In [ ]:
#split into 80/20 train, test
trainsize = 0.8
split = round(len(ts_weekly)*trainsize)
ts_train = ts_weekly.iloc[:split]
ts_test = ts_weekly.iloc[split:]

fig,ax= plt.subplots(figsize=(12,8))
kws = dict(marker='o')
plt.plot(ts_train, label='Train', **kws)
plt.plot(ts_test, label='Test', **kws)
ax.legend(bbox_to_anchor=[1,1]);

In [ ]:
#run autoarima to model time series
ts_autoarima = auto_arima(ts_train, start_p=0, start_q=0,
                          information_criterion='aic', max_d=4, max_q=4,
                          max_p=4, start_P=0, start_Q=0, max_P=4, max_Q=4,
                          max_D=4, trace=True, stepwise=True)

In [ ]:
ts_autoarima.summary()

Model returned 4 AR terms, 1 MA term, and 1 sigma term. AIC was minimized to 2088.818 using the auto_arima package's stepwise search.

In [ ]:
#visulaize model
ts_autoarima.plot_diagnostics(figsize=(22,15))
plt.show()

In [ ]:
#predict over test period
ts_preds = ts_autoarima.predict(n_periods=ts_test.shape[0], return_conf_int=True)

In [ ]:
d = ts_preds[0]
print(d)

In [ ]:
#put forecasts in DF
ts_forecastdf = pd.DataFrame(d, columns=['prediction'])
ts_forecastdf

In [ ]:
ts_forecastdf.isnull().value_counts()

In [ ]:
#


In [ ]:
#visualize prediction
pd.concat([ts_weekly['payment_value'], ts_forecastdf], axis=1).plot()

In [ ]:
periods = ts_forecastdf.shape[0] + 52
periods

In [ ]:
#forecast 1 year into future
ts_future_forecast = ts_autoarima.predict(n_periods=periods, return_conf_int=True)

In [ ]:
#forecast horizon of 1 year
ts_forecast_range = pd.date_range(start='2018-04-02', 
                                  periods=periods,
                                 freq='W') #three years

In [ ]:
#define confidence intervals
lower_r5 = pd.Series(ts_future_forecast[1][:,0], index=ts_forecast_range)
upper_r5 = pd.Series(ts_future_forecast[1][:,1], index=ts_forecast_range)

In [ ]:
#put forecasts in DF
ts_future_forecastdf = pd.DataFrame(ts_future_forecast[0], index=ts_forecast_range,
                                   columns=['prediction'])

In [ ]:
#visualize prediction
pd.concat([ts_weekly, ts_future_forecastdf], axis=1).plot()

In [ ]:
#visualize forecasts with confidence intervals
plt.plot(ts_weekly)
plt.plot(ts_future_forecastdf, color='darkgreen')
plt.fill_between(ts_forecast_range,
                lower_r5,
                upper_r5,
                color='k', alpha=.15)
plt.title('Weekly Sales Prediction')
plt.ticklabel_format(useOffset=False, axis='y', style='plain')
plt.xticks(rotation=70)
plt.tight_layout()

Unusually, our data shows weekly sales dropping off a cliff to zero. This "outlier" event causes some difficulty in our SARIMAX modeling.
<br>

Splitting the data into training and test sets results in the model predicting inaccuratley over the test set. Basically, a 80/20 train-test split results in a SARIMAX model that completely misses the sudden downturn to zero sales. This is because the training data alone does not indicate or suggest such a drastic drop in sales to zero. 
<br>

In fact, a quick google search of Olist 2018 revenue shows no sign of a drop to zero sales. Therefore, this anomaly is probably the result of data collection issues. It is most likely that the data collection of sales revenue was not fully or properly recorded in the dataset provided. 
<br>

Nevertheless, data collection is outside the scope of this project. Therefore, I will re-train the model on the entire dataset. This should yield a better picture of future sales, since the training will take into account the sudden drop in sales that plagues our model validation. 


In [ ]:
#run autoarima to model time series
ts_autoarima_final = auto_arima(ts_weekly, start_p=0, start_q=0,
                          information_criterion='aic', max_d=4, max_q=4,
                          max_p=4, start_P=0, start_Q=0, max_P=4, max_Q=4,
                          max_D=4, trace=True, stepwise=True)

In [ ]:
ts_autoarima_final.summary()

Model returned 2 AR terms, 1 sigma term, and 2 MA terms (2, 1, 2). AIC was minimized to 2623.873 through auto_arima package's stepwise search. 

In [ ]:
#visulaize model
ts_autoarima_final.plot_diagnostics(figsize=(22,15))
plt.show()

In [ ]:
#predict over 1 year period
ts_preds_final = ts_autoarima_final.predict(n_periods=52, return_conf_int=True)

In [ ]:
d_final = ts_preds_final[0]
print(d_final)

In [ ]:
#put forecasts in DF
ts_forecastdf_final = pd.DataFrame(d_final, columns=['prediction'])
ts_forecastdf_final

In [ ]:
#visualize prediction
pd.concat([ts_weekly, ts_forecastdf_final], axis=1).plot()

In [ ]:
#forecast horizon of 1 year
ts_forecast_range_final = pd.date_range(start='2018-09-16', 
                                  periods=52,
                                 freq='W') 

In [ ]:
#define confidence intervals
lower_r5_final = pd.Series(ts_preds_final[1][:,0], index=ts_forecast_range_final)
upper_r5_final = pd.Series(ts_preds_final[1][:,1], index=ts_forecast_range_final)

In [ ]:
#visualize forecasts with confidence intervals
plt.plot(ts_weekly)
plt.plot(ts_forecastdf_final, color='darkgreen')
plt.fill_between(ts_forecast_range_final,
                lower_r5_final,
                upper_r5_final,
                color='k', alpha=.15)
plt.title('Weekly Sales Prediction - Trained on Entire Dataset')
plt.ticklabel_format(useOffset=False, axis='y', style='plain')
plt.xticks(rotation=70)
plt.tight_layout()

The model trained on the entire dataset is visualized above with the 95% confidence interval of the predictions shaded in grey. The model predicts a bounce back of sales, which stabilize around 147K. 
<br>

However, the prediction line should not be considered alone. The confidence interval of the prediction provides a range that weekly predictions should fall into according to the model. The lower side of the interval indicates zero or near zero sales. The upper side indicates a possible return to healthier sales numbers. That being said, confidence intervals do not represent an "upper" situation vs. a "lower" situation. They simply represent <b>a range</b> that the model is 95% confident the true value of the prediction lies within. 

# Business Recommendations: Capital Allocations, Customer Lifetime Value, and Reccuring Revenue

## GeoSpatial Recommendations
<br>
<b> 1. Invest in building out operations in Bahia, a region close to our hub of operations in the south with the third largest population in Brazil (after SP, MG). </b> According to our geospatial analysis, Bahia has the potential to become one of Olist's core geographies. The region already has healthy traction in sales, freight value, and delivery rates. Moreover, Bahia's proximity to Olist's hub of operations in Sao Paulo allows for an easier transfer of transportation assets and personel. Managers should focus on increasing sales from the region, along with increasing the number of sellers. More local sellers in Bahia should maintain healthier delivery times and strong delivery rates. Bahia is not as dense as other Olist core geographies, so local sellers is important for more efficent deliveries. 
<br>

<b> 2. Invest in operations in Paraná.</b> Similar to Bahia, Paraná has a large population with close proximity to our hub of operations. Sales, freight values, and seller count suggest that Paraná could also become a core geography for Olist. While Paraná has a lower total population than Bahia, Paraná is nearly twice as dense. For Olist, this means less average distanced traveled for delivery, as customers will be more concentrated.
<br>

These recommendations are aligned with the goal of growing sales revenue and seller counts across southern Brazil. Southern Brazil has multiple important population centers surrounding Olist's hub of operations in Sao Paulo. Building out operations in the south should be a first priority. Thinking more broadly, Olist's capital allocations should be concentrated in the south and move north towards the northeast population centers as the southern markets mature. 

## Clustering Recommendations
<br>

<b>1. Create targeted upsell recommendations for customers during checkout in order to increase average order value.</b>
<br>
Our largest customer segment (cluster 0 at 83K customers) has a meager BR $143 average order value (AOV). By providing relevant, targeted upsells using a recommendation model, Olist managers will increase AOV and drive more profitability across cluster 0. The recommendation upsell model should be implemented in browser during checkout, as well as emailed in a preprogrammed, post-purchase email flow. 
<br>
The email flow should be structured as follows:
<br>
>Post Purchase "Thank You" plus reccomendations
<br>
>"You forgot these" reminder with recommendations
<br>
>"Order now and save X%" with recommendations (introduce some urgency, final push for purchasing)

<br>

<b>2. Build out an SMS list to recapture customers and increase customer lifetime value.</b> Olist can collect phone numbers as a part of the checkout process, or test browser pop-ups that ask for phone numbers and emails. Open rates for SMS marketing communications are significnatly higher than regular email. Successful SMS campaigns can reach open rates of up to 90%, while email open rates usually sit around 30%. Consumers can enjoy a more personal touchpoint with the Olist brand via SMS.
<br>
Periodic SMS campaigns offering discounts, announcing new product offerings, or promoting events (holiday sales, black friday, etc.) should increase the frequency of buyers, resulting in an increase of customer lifetime value. However, SMS campaigns should not exceed 4-6 texts per month. We do not want our customers to interpret our SMS communications as spam, so the frequency should not exceed the prescribed limit. 
<br>
<br>
Overall, these two recommendations seek to address the underlying, existential problem revealed by our clustering: <b>low customer lifetime value.</b> Targeted email upsells alongside SMS campaigns should increase the frequency of buying, as well as the average order value. Metrics of evaluation include the average order value of our largest customer segment (cluster 0), and the frequency of buying across all our clusters. 

## Time Series Analysis Recommendation
<br>
<b>1. Build out an Olist paid membership program in order to provide more stable, reccuring monthly revenue.</b> Olist's sales revenue over the examined period had multiple drastic fluctutations, including a sudden drop to zero. Olist memberships could provide some predictability and stability in Olist's revenue structure. This will give managers more stable cashflow, allowing them to make more informed decisions on capital allocation. Relying on wildly swinging sales complicates a manager's ability to make effective decisions on growth, hiring, scaling, etc. 
<br>

# Limitations and Next Steps
<br>
The next step in executing on the recommendations provided would be a comprehensive review of the Paraná and Bahia regions. Financial and logistics information should be compiled and analyzed to ascertain the feasability of investing more heavily in these regions. Analysis should review historic return on invested capital in those regions, as well as model the performance of future investments. Does Olist have the logistics in place to handle more capacity? Do investments in these regions make sense at the current cost of capital? Is it better to buy or build the systems needed to increase revenue? 
<br>

Second, the success of our customer lifetime value campaigns should be monitored and evaluated. Relevant success metrics include average order value, frequency, recency, and customer lifetime value. Meaningful lift in these metrics would signal success.

